## Final project for the capstone : 2 hours @ Paris

#### This proejct will use the data mainly from two site: Wikipedia and the Paris data (https://opendata.paris.fr/page/home/). The Paris Data is a open source site which has a full package information to explorer the city, with data file (almost all format) that anyone can download, so my project will use the basic library and the site supplied data.

#### For my proposal and details of this project, please refer to the document that I uploaded for the PGA link, here I write only the coding part.

#### 1. Preparation Python

In [1]:
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
import csv
import json
import xml
!conda install -c conda-forge folium=0.5.0 --yes
import folium
from folium import plugins
import json
from pprint import pprint
!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim
from IPython.display import Image 
from IPython.core.display import HTML 
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
import requests
from pandas.io.json import json_normalize

Solving environment: \ 
The environment is inconsistent, please check the package plan carefully
The following packages are causing the inconsistency:

  - defaults/linux-64::anaconda==5.3.1=py37_0
  - defaults/linux-64::astropy==3.0.4=py37h14c3975_0
  - defaults/linux-64::bkcharts==0.2=py37_0
  - defaults/linux-64::blaze==0.11.3=py37_0
  - defaults/linux-64::bokeh==0.13.0=py37_0
  - defaults/linux-64::bottleneck==1.2.1=py37h035aef0_1
  - defaults/linux-64::dask==0.19.1=py37_0
  - defaults/linux-64::datashape==0.5.4=py37_1
  - defaults/linux-64::mkl-service==1.1.2=py37h90e4bf4_5
  - defaults/linux-64::numba==0.39.0=py37h04863e7_0
  - defaults/linux-64::numexpr==2.6.8=py37hd89afb7_0
  - defaults/linux-64::odo==0.5.1=py37_0
  - defaults/linux-64::pytables==3.4.4=py37ha205bf6_0
  - defaults/linux-64::pytest-arraydiff==0.2=py37h39e3cac_0
  - defaults/linux-64::pytest-astropy==0.4.0=py37_0
  - defaults/linux-64::pytest-doctestplus==0.1.3=py37_0
  - defaults/linux-64::pywavelets==1.0.0=py37h

#### 2 Data

#### 2.1 Data preparation

#### 2.1.1 use the  wikipedia link to get the Paris information

In [2]:
url = requests.get('https://en.wikipedia.org/wiki/Arrondissements_of_Paris#Arrondissements').text

In [3]:
# save the script for variable or mapping searching
soup = BeautifulSoup(url, 'lxml')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Arrondissements of Paris - Wikipedia
  </title>
  <script>
   document.documentElement.className=document.documentElement.className.replace(/(^|\s)client-nojs(\s|$)/,"$1client-js$2");RLCONF={"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"Arrondissements_of_Paris","wgTitle":"Arrondissements of Paris","wgCurRevisionId":899828883,"wgRevisionId":899828883,"wgArticleId":1175882,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["CS1 French-language sources (fr)","Articles with short description","Use dmy dates from March 2016","Arrondissements of Paris","Government of Paris"],"wgBreakFrames":!1,"wgPageContentLanguage":"en","wgPageContentModel":"wikitext","wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","Fe

In [4]:
arrond_table = soup.find("table", class_ = 'wikitable sortable')
arrond_table_rows = arrond_table.find_all('tr')

In [5]:
# Information collecting & split
information = []
for row in arrond_table_rows:
    info = row.text.split('\n')[1:-1]
    information.append(info)
del information[0][1::2]
information

[['Arrondissement (R for Right Bank, L for Left Bank)',
  'Name',
  'Area (km2)',
  'Population(March 1999 census)',
  'Population(July 2005 estimate)',
  'Density (2005)(inhabitants per km2)',
  'Peak of population',
  'Mayor'],
 ['1st (Ie) R',
  'Louvre',
  '1.826\xa0km2 (0.705\xa0sq\xa0mi)',
  '16,888',
  '17,700',
  '9,693',
  'before 1861',
  'Jean-François Legaret'],
 ['2nd (IIe) R',
  'Bourse',
  '0.992\xa0km2 (0.383\xa0sq\xa0mi)',
  '19,585',
  '20,700',
  '20,867',
  'before 1861',
  'Jacques Boutault'],
 ['3rd (IIIe) R',
  'Temple',
  '1.171\xa0km2 (0.452\xa0sq\xa0mi)',
  '34,248',
  '35,100',
  '29,974',
  'before 1861',
  'Pierre Aidenbaum'],
 ['4th (IVe) R',
  'Hôtel-de-Ville',
  '1.601\xa0km2 (0.618\xa0sq\xa0mi)',
  '30,675',
  '28,600',
  '17,864',
  'before 1861',
  'Christophe Girard'],
 ['5th (Ve) L',
  'Panthéon',
  '2.541\xa0km2 (0.981\xa0sq\xa0mi)',
  '58,849',
  '60,600',
  '23,849',
  '1911',
  'Florence Berthout'],
 ['6th (VIe) L',
  'Luxembourg',
  '2.154\xa0km

In [6]:
# creation dataframe to have the detailed informations by districts in columns 
arrond_df = pd.DataFrame(information[1:], columns=information[0])
arrond_df.head()

Arrondissement (R for Right Bank, L for Left Bank)            Name  \
0                                         1st (Ie) R          Louvre   
1                                        2nd (IIe) R          Bourse   
2                                       3rd (IIIe) R          Temple   
3                                        4th (IVe) R  Hôtel-de-Ville   
4                                         5th (Ve) L        Panthéon   

                Area (km2) Population(March 1999 census)  \
0  1.826 km2 (0.705 sq mi)                        16,888   
1  0.992 km2 (0.383 sq mi)                        19,585   
2  1.171 km2 (0.452 sq mi)                        34,248   
3  1.601 km2 (0.618 sq mi)                        30,675   
4  2.541 km2 (0.981 sq mi)                        58,849   

  Population(July 2005 estimate) Density (2005)(inhabitants per km2)  \
0                         17,700                               9,693   
1                         20,700                              20,867   
2                         35,100                              29,974   
3                         28,600                              17,864   
4                         60,600                              23,849   

  Peak of population                  Mayor  
0        before 1861  Jean-François Legaret  
1        before 1861       Jacques Boutault  
2        before 1861       Pierre Aidenbaum  
3        before 1861      Christophe Girard  
4               1911      Florence Berthout

In [7]:
# name the Arrondissement and show the result
arrond_number = ['1st', '2nd', '3rd', '4th', '5th', '6th', '7th', '8th', '9th','10th',
                '11th', '12th', '13th', '14th', '15th', '16th', '17th', '18th', '19th', '20th']
Arr = pd.DataFrame({'Arrondissement': arrond_number})
arrond_df = pd.concat([arrond_df, Arr], axis = 1)
arrond_df.head()

Arrondissement (R for Right Bank, L for Left Bank)            Name  \
0                                         1st (Ie) R          Louvre   
1                                        2nd (IIe) R          Bourse   
2                                       3rd (IIIe) R          Temple   
3                                        4th (IVe) R  Hôtel-de-Ville   
4                                         5th (Ve) L        Panthéon   

                Area (km2) Population(March 1999 census)  \
0  1.826 km2 (0.705 sq mi)                        16,888   
1  0.992 km2 (0.383 sq mi)                        19,585   
2  1.171 km2 (0.452 sq mi)                        34,248   
3  1.601 km2 (0.618 sq mi)                        30,675   
4  2.541 km2 (0.981 sq mi)                        58,849   

  Population(July 2005 estimate) Density (2005)(inhabitants per km2)  \
0                         17,700                               9,693   
1                         20,700                              20,867   
2                         35,100                              29,974   
3                         28,600                              17,864   
4                         60,600                              23,849   

  Peak of population                  Mayor Arrondissement  
0        before 1861  Jean-François Legaret            1st  
1        before 1861       Jacques Boutault            2nd  
2        before 1861       Pierre Aidenbaum            3rd  
3        before 1861      Christophe Girard            4th  
4               1911      Florence Berthout            5th

In [8]:
arrond_df.dtypes

Arrondissement (R for Right Bank, L for Left Bank)    object
Name                                                  object
Area (km2)                                            object
Population(March 1999 census)                         object
Population(July 2005 estimate)                        object
Density (2005)(inhabitants per km2)                   object
Peak of population                                    object
Mayor                                                 object
Arrondissement                                        object
dtype: object

In [9]:
landmarks = ['Cathédrale Notre-Dame de Paris', 'Arc de Triomphe', 'Centre Pompidou',
             'Sacré-Cœur Basilica', 'Eiffel Tower',
             'The Louvre', 'La Grande Arche', 'Les Invalides', 'Fondation Louis Vuitton',
             'Panthéon', 'Picasso Museum', 'Cinémathèque Française',
             'Opéra Garnier', 'The Grand Palais', 'Hôtel de Ville',
             'Fondation Cartier', 'Jeu de Paume', 'Jardin des Plantes',
             'Fondation Jerôme Seydoux-Pathé', 'Île de la Cité',
             'The Palais de Tokyo', 'Philharmonie de Paris', 'Musée d’Orsay',
             'Palais du Luxembourg', 'Montmartre', 'Champs-Élysées',
             'Palace of Versailles', 'Tuileries Garden', 'Moulin Rouge',
             'Disneyland Paris', 'Place de la Concorde', 'Catacombs of Paris',
             'Rodin Museum', 'Île de la Cité', 'Orangerie Museum', 'Pont des Arts',
             'Île Saint-Louis', 'Place Vendôme', 'Saint-Jacques Tower', 'La Conciergerie',
            ]

landmarks_df = pd.DataFrame({'Landmark': landmarks})

In [10]:
def landmark_loc(list_of_landmarks):
    for place in list_of_landmarks:
        address = (place)
        geolocator = Nominatim(user_agent="Paris_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        print('{''}, {}, {},'.format(place,latitude,longitude))

landmark_loc(landmarks)

Cathédrale Notre-Dame de Paris, 48.85293705, 2.3500501225,
Arc de Triomphe, 48.8737791, 2.29503722603767,
Centre Pompidou, 48.8605918, 2.35247431766534,
Sacré-Cœur Basilica, 48.88680575, 2.34301534488351,
Eiffel Tower, 48.8582602, 2.29449905431968,
The Louvre, 48.8611473, 2.33802768704666,
La Grande Arche, 43.1844505, 5.5748974,
Les Invalides, 48.8570374, 2.3118779,
Fondation Louis Vuitton, 48.87665005, 2.26333809580246,
Panthéon, 48.8454189, 2.3525815263157,
Picasso Museum, 41.3851066, 2.18120508674285,
Cinémathèque Française, 48.8369987, 2.38263520273537,
Opéra Garnier, 48.87203085, 2.3317901855896,
The Grand Palais, 48.86616135, 2.31222295966943,
Hôtel de Ville, 43.9492974, 4.80526012041732,
Fondation Cartier, 48.8373182, 2.33193184219906,
Jeu de Paume, 48.8658156, 2.32408776132074,
Jardin des Plantes, 48.8432224, 2.35950895709484,
Fondation Jerôme Seydoux-Pathé, 48.8334765, 2.35490681339522,
Île de la Cité, 48.85470505, 2.3474846899114,
The Palais de Tokyo, 48.8639905, 2.2965215131

In [11]:
landmarks_loc = ['Cathédrale Notre-Dame de Paris', 48.85293695, 2.35005149954546,
'Arc de Triomphe', 48.8737791, 2.29503722603767,
'Centre Pompidou', 48.8605918, 2.35247431766534,
'Sacré-Cœur Basilica', 48.88680575, 2.34301534488351,
'Eiffel Tower', 48.8582602, 2.29449905431968,
'The Louvre', 48.8611473, 2.33802768704666,
'La Grande Arche', 48.8930151, 2.2376206,
'Les Invalides', 48.8570374, 2.3118779,
'Fondation Louis Vuitton', 48.87665005, 2.26333809580246,
'Panthéon', 48.8454189, 2.35258442491778,
'Picasso Museum', 41.3851066, 2.18120508674285,
'Cinémathèque Française', 48.8369987, 2.38263520273537,
'Opéra Garnier', 48.87203085, 2.3317901855896,
'The Grand Palais', 48.86616135, 2.31222295966943,
'Hôtel de Ville', 43.9492974, 4.80526012041732,
'Fondation Cartier', 48.8373182, 2.33193184219906,
'Jeu de Paume', 48.8658156, 2.32408776132074,
'Jardin des Plantes', 48.8432224, 2.35950895709484,
'Fondation Jerôme Seydoux-Pathé', 48.8334765, 2.35490681339522,
'Île de la Cité', 48.85470505, 2.3474846899114,
'The Palais de Tokyo', 48.8639905, 2.29652151313114,
'Philharmonie de Paris', 48.89192125, 2.39413864295307,
'Musée d’Orsay', 48.85991785, 2.32658283469656,
'Palais du Luxembourg', 48.84852845, 2.33683647732996,
'Montmartre', 46.8021347, -0.7198939,
'Champs-Élysées', 48.8707573, 2.3053312,
'Palace of Versailles', 48.80442525, 2.1202852709926,
'Tuileries Garden', 48.86366215, 2.32683861305756,
'Moulin Rouge', 48.8840787, 2.3324082,
'Disneyland Paris', 48.8711359, 2.77612651196751,
'Place de la Concorde', 29.9002052, -90.0095146,
'Catacombs of Paris', 48.833964, 2.3324924,
'Rodin Museum', 39.9619295, -75.1739508,
'Île de la Cité', 48.85470505, 2.3474846899114,
'Orangerie Museum', 48.8637655, 2.32266020780693,
'Pont des Arts', 48.8578114, 2.3372459,
'Île Saint-Louis', 48.85161305, 2.35673414953666,
'Place Vendôme', 48.8674634, 2.32942811682519,
'Saint-Jacques Tower', 48.8580032, 2.34892171290132,
'La Conciergerie', 48.8559492, 2.3460263]

landmarks_df = pd.DataFrame(np.array(landmarks_loc).reshape(40, 3), columns = ["Landmark","Latitude","Longitude"])

# Change the latitude and longitude to a float
landmarks_df['Latitude'] = landmarks_df.Latitude.astype(float)
landmarks_df['Longitude'] = landmarks_df.Longitude.astype(float)

In [12]:
arrond_list = arrond_df['Arrondissement'].unique()
arrond_list

def landmark_loc(list_of_arronds):
    for place in list_of_arronds:
        address = (place + ' Arrondissement')
        geolocator = Nominatim(user_agent="arrond_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        print('{}, {}, {},'.format(place,latitude,longitude))

landmark_loc(arrond_list)

1st, 48.8646144, 2.334396,
2nd, 48.868743, 2.341688,
3rd, 48.864212, 2.360936,
4th, 48.8562021, 2.3556193,
5th, 48.8460591, 2.3445228,
6th, 48.8504333, 2.3329507,
7th, 48.8570281, 2.3201953,
8th, 48.8773158, 2.3172611,
9th, 48.876019, 2.339962,
10th, 48.876106, 2.35991,
11th, 48.858416, 2.379703,
12th, 48.8396154, 2.3957517,
13th, 48.8323973, 2.3555829,
14th, 48.8330589, 2.3269591,
15th, 48.8413705, 2.3003827,
16th, 48.8631709, 2.2757648,
17th, 48.8842239, 2.3223639,
18th, 48.8900117, 2.3464668,
19th, 48.889343, 2.38436,
20th, 48.865042, 2.398929,


In [13]:
arrond_list = arrond_df['Arrondissement'].unique()
arrond_list

def landmark_loc(list_of_arronds):
    LL = []
    for place in list_of_arronds:
        address = (place + ' Arrondissement')
        geolocator = Nominatim(user_agent="arrond_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        LL.append(place)
        LL.append(latitude)
        LL.append(longitude)
    print(LL)


LL = landmark_loc(arrond_list)

['1st', 48.8646144, 2.334396, '2nd', 48.868743, 2.341688, '3rd', 48.864212, 2.360936, '4th', 48.8562021, 2.3556193, '5th', 48.8460591, 2.3445228, '6th', 48.8504333, 2.3329507, '7th', 48.8570281, 2.3201953, '8th', 48.8773158, 2.3172611, '9th', 48.876019, 2.339962, '10th', 48.876106, 2.35991, '11th', 48.858416, 2.379703, '12th', 48.8396154, 2.3957517, '13th', 48.8323973, 2.3555829, '14th', 48.8330589, 2.3269591, '15th', 48.8413705, 2.3003827, '16th', 48.8631709, 2.2757648, '17th', 48.8842239, 2.3223639, '18th', 48.8900117, 2.3464668, '19th', 48.889343, 2.38436, '20th', 48.865042, 2.398929]


In [14]:
LL = ['1st', 48.8646144, 2.334396, '2nd', 48.868743, 2.341688, '3rd', 48.864212, 2.360936, 
      '4th', 48.8562021, 2.3556193, '5th', 48.8460591, 2.3445228, '6th', 48.8504333, 2.3329507, 
      '7th', 48.8570281, 2.3201953, '8th', 48.8773158, 2.3172611, '9th', 48.876019, 2.339962, 
      '10th', 48.876106, 2.35991, '11th', 48.858416, 2.379703, '12th', 48.8396154, 2.3957517, 
      '13th', 48.8323973, 2.3555829, '14th', 48.8330589, 2.3269591, '15th', 48.8413705, 2.3003827, 
      '16th', 48.8631709, 2.2757648, '17th', 48.8842239, 2.3223639, '18th', 48.8900117, 2.3464668, 
      '19th', 48.889343, 2.38436, '20th', 48.865042, 2.398929]

In [15]:
arrond_LL = pd.DataFrame(np.array(LL).reshape(20,3), columns = ["Arrondissement","Latitude","Longitude"])
arrond_LL['Latitude'] = arrond_LL.Latitude.astype(float)
arrond_LL['Longitude'] = arrond_LL.Longitude.astype(float)
arrond_LL

Arrondissement   Latitude  Longitude
0             1st  48.864614   2.334396
1             2nd  48.868743   2.341688
2             3rd  48.864212   2.360936
3             4th  48.856202   2.355619
4             5th  48.846059   2.344523
5             6th  48.850433   2.332951
6             7th  48.857028   2.320195
7             8th  48.877316   2.317261
8             9th  48.876019   2.339962
9            10th  48.876106   2.359910
10           11th  48.858416   2.379703
11           12th  48.839615   2.395752
12           13th  48.832397   2.355583
13           14th  48.833059   2.326959
14           15th  48.841370   2.300383
15           16th  48.863171   2.275765
16           17th  48.884224   2.322364
17           18th  48.890012   2.346467
18           19th  48.889343   2.384360
19           20th  48.865042   2.398929

#### 2.1.2 Use Paris Open data source to load GEOJSON

In [17]:
with open('arrondissements.geojson') as file:    
    paris = json.load(file)
paris

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[2.351518483670821, 48.8644258050741],
      [2.350949105218923, 48.86340592861751],
      [2.346676032763327, 48.864430925901665],
      [2.346675453051013, 48.86443106483368],
      [2.345101655171463, 48.864809197959836],
      [2.341271025930368, 48.86572767724484],
      [2.34126849090564, 48.86572828653819],
      [2.341204510696185, 48.865743681005995],
      [2.341178272058699, 48.86574963323163],
      [2.341083555178273, 48.86577201721946],
      [2.337371969067098, 48.86664907439458],
      [2.335869691238243, 48.86699647535598],
      [2.335869054057415, 48.86699662650754],
      [2.333675321300195, 48.867516125009374],
      [2.33172601351949, 48.867954816599685],
      [2.331725629348361, 48.86795490259037],
      [2.330656733960091, 48.86819218066118],
      [2.330306795320876, 48.86835619167468],
      [2.329965588686572, 48.86851416917429],
      [2.3

In [18]:
address = ('Paris, France')
geolocator = Nominatim(user_agent="Paris_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('{''}, {}, {},'.format(address,latitude,longitude))

Paris, France, 48.8566101, 2.3514992,


In [19]:
paris_lat = 48.8566101
paris_long = 2.3514992

paris_map = folium.Map(location=[paris_lat, paris_long], zoom_start = 12)
paris_map

In [20]:
arronds_map = folium.Map(location = [paris_lat, paris_long], zoom_start = 14)

arronds_map.choropleth(
    geo_data=paris,
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.1, 
    line_opacity=0.8,
)

for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'Yellow',
        fill_opacity = 0.9,
        parse_html = False).add_to(arronds_map)
        
arronds_map

In [21]:
# mapping the geojson key with the district name
arrond_new = ['1er Arrondissement', '2e Arrondissement','3e Arrondissement',
             '4e Arrondissement', '5e Arrondissement', '6e Arrondissement', 
             '7e Arrondissement', '8e Arrondissement','9e Arrondissement',
             '10e Arrondissement', '11e Arrondissement', '12e Arrondissement', 
             '13e Arrondissement', '14e Arrondissement', '15e Arrondissement',
             '16e Arrondissement', '17e Arrondissement', '18e Arrondissement', 
             '19e Arrondissement', '20e Arrondissement']

population_2005 = [17700, 20700, 35100, 28600, 60600,
45200,55400,38700,58500,88800,152500,138300,181300,134700,
232400,149500,160300,188700,187200,191800]

pop_2005 = pd.DataFrame({'Arrondissement': arrond_new, 'Population': population_2005})

In [22]:
Paris_map = folium.Map(location = [paris_lat, paris_long], zoom_start = 14)

Paris_map.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='Blues', 
    fill_opacity=0.6, 
    line_opacity=0.6,
    legend_name='Population by Arrondissement in Paris 2005'
)

Paris_map

In [23]:
paris_map_v2 = folium.Map(location = [paris_lat, paris_long], zoom_start = 12)

paris_map_v2.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.5, 
    line_opacity=0.2,
    legend_name='Population by Arrondissement in Paris 2005'
)

#add neighborhood markers to the Paris map
for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'Yellow',
        fill_opacity = 0.7,
        parse_html = False).add_to(paris_map_v2)
        

# display map
paris_map_v2

In [24]:
from folium import IFrame

paris_map_v3 = folium.Map(location = [paris_lat, paris_long], zoom_start = 12)

paris_map_v3.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.5, 
    line_opacity=0.2,
    legend_name='Population by Arrondissement in Paris 2005'
)

for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    iframe = folium.IFrame(label, width=700, height=450)
    label = folium.Popup(iframe, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(paris_map_v3)
        
paris_map_v3

In [25]:
map_landmarks = folium.Map(location = [paris_lat, paris_long], zoom_start = 10)

map_landmarks.choropleth(
    geo_data=paris,
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.1, 
    line_opacity=0.8,
)

#add neighborhood markers to the Paris map
for lat, long, landmark in zip(landmarks_df['Latitude'], landmarks_df['Longitude'], 
                                 landmarks_df['Landmark']):
    label = '{}'.format(landmark)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(map_landmarks)
        
map_landmarks

In [26]:
map_landmarks2 = folium.Map(location = [paris_lat, paris_long], zoom_start = 10)

map_landmarks2.choropleth(
    geo_data=paris,
    data=pop_2005,
    columns=['Arrondissement', 'Population'],
    key_on='feature.properties.nom',
    fill_color='PuBu', 
    fill_opacity=0.1, 
    line_opacity=0.5,
)

#add landmarks markers to the Paris map
for lat, long, landmark in zip(landmarks_df['Latitude'], landmarks_df['Longitude'], 
                                 landmarks_df['Landmark']):
    label = '{}'.format(landmark)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 7, 
        popup = label,
        color = 'red',
        fill = True,
        fill_color = 'blue',
        fill_opacity = 0.7,
        parse_html = False).add_to(map_landmarks2)
    
#add neighborhood markers to the Paris map
for lat, long, arrond in zip(arrond_LL['Latitude'], arrond_LL['Longitude'], 
                                 arrond_LL['Arrondissement']):
    label = '{}'.format(arrond)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius = 5, 
        popup = label,
        color = 'white',
        fill = True,
        fill_color = 'green',
        fill_opacity = 0.5,
        parse_html = False).add_to(map_landmarks2)
        
map_landmarks2

#### 2.1.3 Use foursquare data

In [27]:
CLIENT_ID = 'NBGXQTF5JJ5EQZHXHXZCG2AABE4C20W5JXQ25XXSXNM34F0C' # your Foursquare ID
CLIENT_SECRET = 'NW2Q1KMTFNFR4EJCCS1W5OUCA5INYO1Z0QPJUG3KOPH2DXJS' # your Foursquare Secret
VERSION = '20180605'

In [29]:
# DF for the popular district
popular_arrond = arrond_LL[arrond_LL['Arrondissement'].isin(
    ['1st', '3rd', '4th', '5th', '6th', '7th', '8th', '18th'])]

popular_arrond

Arrondissement   Latitude  Longitude
0             1st  48.864614   2.334396
2             3rd  48.864212   2.360936
3             4th  48.856202   2.355619
4             5th  48.846059   2.344523
5             6th  48.850433   2.332951
6             7th  48.857028   2.320195
7             8th  48.877316   2.317261
17           18th  48.890012   2.346467

In [30]:
arrond_1_lat = arrond_LL.iloc[0,1]

arrond_1_long = arrond_LL.iloc[0,2]

LIMIT = 250

radius = 2000

url1 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    arrond_1_lat, 
    arrond_1_long, 
    VERSION, 
    radius, 
    LIMIT)

url1

'https://api.foursquare.com/v2/venues/explore?client_id=NBGXQTF5JJ5EQZHXHXZCG2AABE4C20W5JXQ25XXSXNM34F0C&client_secret=NW2Q1KMTFNFR4EJCCS1W5OUCA5INYO1Z0QPJUG3KOPH2DXJS&ll=48.8646144,2.334396&v=20180605&radius=2000&limit=250'

In [31]:
results1 = requests.get(url1).json()
results1

{'meta': {'code': 200, 'requestId': '5cf4cbbfdd57970e4d4f77e3'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Palais-Royal',
  'headerFullLocation': 'Palais-Royal, Paris',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 242,
  'suggestedBounds': {'ne': {'lat': 48.88261441800002,
    'lng': 2.3617071938645045},
   'sw': {'lat': 48.846614381999984, 'lng': 2.3070848061354954}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4f0b706de5e8207020057ed7',
       'name': 'Sanukiya',
       'location': {'address': "9 rue d'Argenteuil",
        'lat': 48.86471330060748,
        'lng': 2.333805151283741,
        'labeledLatLngs': [{'label': 'display',
          'lat': 48.8

In [33]:
def getNearbyVenues(names, latitudes, longitudes, radius, LIMIT):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])
            

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Arrondissement', 
                  'Arrondissement Latitude', 
                  'Arrondissement Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

popular_arrond_venues = getNearbyVenues(names=popular_arrond['Arrondissement'],
                                   latitudes=popular_arrond['Latitude'],
                                   longitudes=popular_arrond['Longitude'],
                                   radius=2000, LIMIT=300
                                  )

1st
3rd
4th
5th
6th
7th
8th
18th


In [34]:
arrond_venues = getNearbyVenues(names=arrond_LL['Arrondissement'],
                                   latitudes=arrond_LL['Latitude'],
                                   longitudes=arrond_LL['Longitude'],
                                   radius=2000, LIMIT=300
                                  )

1st
2nd
3rd
4th
5th
6th
7th
8th
9th
10th
11th
12th
13th
14th
15th
16th
17th
18th
19th
20th


In [36]:
print(arrond_venues.shape)
arrond_venues.head()

(2000, 7)


Arrondissement  Arrondissement Latitude  Arrondissement Longitude  \
0            1st                48.864614                  2.334396   
1            1st                48.864614                  2.334396   
2            1st                48.864614                  2.334396   
3            1st                48.864614                  2.334396   
4            1st                48.864614                  2.334396   

                    Venue  Venue Latitude  Venue Longitude     Venue Category  
0                Sanukiya       48.864713         2.333805    Udon Restaurant  
1  Jardin du Palais Royal       48.864941         2.337728             Garden  
2        Brasserie Réjane       48.865486         2.334824         Restaurant  
3               Ellsworth       48.865528         2.337057  French Restaurant  
4                Nolinski       48.865367         2.334584              Hotel

In [37]:
arrond_venues = arrond_venues.drop_duplicates(subset=['Venue'], keep = 'first')

In [38]:
arrond_venues.groupby('Arrondissement').count()

Arrondissement Latitude  Arrondissement Longitude  Venue  \
Arrondissement                                                             
10th                                 23                        23     23   
11th                                 67                        67     67   
12th                                 81                        81     81   
13th                                 85                        85     85   
14th                                 78                        78     78   
15th                                 79                        79     79   
16th                                 94                        94     94   
17th                                 35                        35     35   
18th                                 51                        51     51   
19th                                 94                        94     94   
1st                                  99                        99     99   
20th                                 73                        73     73   
2nd                                  31                        31     31   
3rd                                  81                        81     81   
4th                                  36                        36     36   
5th                                  71                        71     71   
6th                                  26                        26     26   
7th                                  27                        27     27   
8th                                  66                        66     66   
9th                                  38                        38     38   

                Venue Latitude  Venue Longitude  Venue Category  
Arrondissement                                                   
10th                        23               23              23  
11th                        67               67              67  
12th                        81               81              81  
13th                        85               85              85  
14th                        78               78              78  
15th                        79               79              79  
16th                        94               94              94  
17th                        35               35              35  
18th                        51               51              51  
19th                        94               94              94  
1st                         99               99              99  
20th                        73               73              73  
2nd                         31               31              31  
3rd                         81               81              81  
4th                         36               36              36  
5th                         71               71              71  
6th                         26               26              26  
7th                         27               27              27  
8th                         66               66              66  
9th                         38               38              38

In [39]:
arrond_onehot = pd.get_dummies(arrond_venues[['Venue Category']], prefix="", prefix_sep="")
arrond_onehot['Arrondissement'] = arrond_venues['Arrondissement'] 
fixed_columns = [arrond_onehot.columns[-1]] + list(arrond_onehot.columns[:-1])
arrond_onehot = arrond_onehot[fixed_columns]
arrond_onehot.head()

Arrondissement  African Restaurant  Arepa Restaurant  \
0            1st                   0                 0   
1            1st                   0                 0   
2            1st                   0                 0   
3            1st                   0                 0   
4            1st                   0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Auvergne Restaurant  BBQ Joint  Bagel Shop  Bakery  Bar  Basketball Court  \
0                    0          0           0       0    0                 0   
1                    0          0           0       0    0                 0   
2                    0          0           0       0    0                 0   
3                    0          0           0       0    0                 0   
4                    0          0           0       0    0                 0   

   Basketball Stadium  Basque Restaurant  Bed & Breakfast  Beer Bar  \
0                   0                  0                0         0   
1                   0                  0                0         0   
2                   0                  0                0         0   
3                   0                  0                0         0   
4                   0                  0                0         0   

   Beer Garden  Beer Store  Bike Rental / Bike Share  Bistro  Boat or Ferry  \
0            0           0                         0       0              0   
1            0           0                         0       0              0   
2            0           0                         0       0              0   
3            0           0                         0       0              0   
4            0           0                         0       0              0   

   Bookstore  Botanical Garden  Boutique  Boxing Gym  Brasserie  \
0          0                 0         0           0          0   
1          0                 0         0           0          0   
2          0                 0         0           0          0   
3          0                 0         0           0          0   
4          0                 0         0           0          0   

   Brazilian Restaurant  Breakfast Spot  Breton Restaurant  Brewery  Bridge  \
0                     0               0                  0        0       0   
1                     0               0                  0        0       0   
2                     0               0                  0        0       0   
3                     0               0                  0        0       0   
4                     0               0                  0        0       0   

   Bubble Tea Shop  Burger Joint  Butcher  Café  Cambodian Restaurant  Canal  \
0                0             0        0     0                     0      0   
1                0             0        0     0                     0      0   
2                0             0        0     0                     0      0   
3                0             0        0     0                     0      0   
4                0             0        0     0                     0      0   

   Caribbean Restaurant  Cemetery  Champagne Bar  Cheese Shop  \
0   

In [40]:
arrond_grouped = arrond_onehot.groupby('Arrondissement').mean().reset_index()
arrond_grouped

Arrondissement  African Restaurant  Arepa Restaurant  \
0            10th            0.000000          0.000000   
1            11th            0.000000          0.000000   
2            12th            0.000000          0.000000   
3            13th            0.000000          0.000000   
4            14th            0.000000          0.000000   
5            15th            0.000000          0.000000   
6            16th            0.000000          0.000000   
7            17th            0.000000          0.000000   
8            18th            0.000000          0.019608   
9            19th            0.000000          0.000000   
10            1st            0.000000          0.000000   
11           20th            0.013699          0.000000   
12            2nd            0.000000          0.000000   
13            3rd            0.000000          0.000000   
14            4th            0.000000          0.000000   
15            5th            0.000000          0.000000   
16            6th            0.000000          0.000000   
17            7th            0.000000          0.000000   
18            8th            0.000000          0.000000   
19            9th            0.000000          0.000000   

    Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0.000000     0.000000    0.000000             0.000000   
1                 0.000000     0.014925    0.014925             0.000000   
2                 0.000000     0.000000    0.000000             0.012346   
3                 0.000000     0.000000    0.000000             0.000000   
4                 0.012821     0.000000    0.012821             0.000000   
5                 0.000000     0.000000    0.000000             0.012658   
6                 0.000000     0.000000    0.042553             0.000000   
7                 0.000000     0.000000    0.000000             0.000000   
8                 0.019608     0.019608    0.000000             0.000000   
9                 0.000000     0.010638    0.000000             0.000000   
10                0.000000     0.020202    0.060606             0.000000   
11                0.000000     0.000000    0.000000             0.000000   
12                0.032258     0.000000    0.032258             0.000000   
13                0.000000     0.024691    0.000000             0.000000   
14                0.000000     0.000000    0.027778             0.000000   
15                0.000000     0.014085    0.014085             0.000000   
16                0.000000     0.000000    0.000000             0.000000   
17                0.000000     0.000000    0.037037             0.000000   
18                0.000000     0.015152    0.015152             0.000000   
19                0.026316     0.000000    0.026316             0.000000   

    Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0               0.000000          0.000000            0.000000   
1               0.000000          0.014925            0.000000   
2               0.000000          0.000000            0.000000   
3               0.000000          0.035294            0.000000   
4               0.000000          0.000000            0.000000   
5               0.000000          0.000000            0.000000   
6               0.010638          0.000000            0.000000   
7               0.000000          0.000000            0.000000   
8               0.000000          0.000000            0.000000   
9               0.000000          0.010638            0.010638   
10              0.000000          0.000000            0.000000   
11              0.000000          0.013699            0.000000   
12              0.000000          0.000000            0.000000   
13              0.000000          0.024691            0.000000   
14              0.000000          0.000000            0.000000   
15              0.000000          0.014085            0.000000   
16              0.000000          0.000000  

In [41]:
num_top_venues = 10

for hood in arrond_grouped['Arrondissement']:
    print("----"+hood+"----")
    temp = arrond_grouped[arrond_grouped['Arrondissement'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----10th----
                 venue  freq
0    French Restaurant  0.13
1               Bakery  0.13
2  Japanese Restaurant  0.09
3      Thai Restaurant  0.04
4           Taco Place  0.04
5            Gastropub  0.04
6           Boxing Gym  0.04
7              Theater  0.04
8          Coffee Shop  0.04
9                Hotel  0.04


----11th----
               venue  freq
0  French Restaurant  0.15
1           Wine Bar  0.09
2        Pizza Place  0.07
3                Bar  0.06
4       Cocktail Bar  0.04
5             Bistro  0.04
6        Coffee Shop  0.03
7           Beer Bar  0.03
8             Bakery  0.03
9               Café  0.03


----12th----
                  venue  freq
0     French Restaurant  0.06
1                  Park  0.04
2                 Hotel  0.04
3           Coffee Shop  0.04
4                Garden  0.04
5  Gym / Fitness Center  0.04
6             Bookstore  0.04
7                   Bar  0.04
8                Bistro  0.02
9             Multiplex  0.02


----13th-

In [42]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [43]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Arrondissement']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
arrond_venues_sorted = pd.DataFrame(columns=columns)
arrond_venues_sorted['Arrondissement'] = arrond_grouped['Arrondissement']

for ind in np.arange(arrond_grouped.shape[0]):
    arrond_venues_sorted.iloc[ind, 1:] = return_most_common_venues(arrond_grouped.iloc[ind, :], num_top_venues)

arrond_venues_sorted

Arrondissement 1st Most Common Venue  2nd Most Common Venue  \
0            10th     French Restaurant                 Bakery   
1            11th     French Restaurant               Wine Bar   
2            12th     French Restaurant              Bookstore   
3            13th     French Restaurant  Vietnamese Restaurant   
4            14th     French Restaurant                  Hotel   
5            15th     French Restaurant                  Hotel   
6            16th     French Restaurant                  Hotel   
7            17th     French Restaurant                  Hotel   
8            18th     French Restaurant     Italian Restaurant   
9            19th     French Restaurant              Multiplex   
10            1st                 Hotel                  Plaza   
11           20th                   Bar      French Restaurant   
12            2nd                 Hotel      French Restaurant   
13            3rd     French Restaurant              Bookstore   
14            4th     French Restaurant            Coffee Shop   
15            5th     French Restaurant                  Plaza   
16            6th                 Hotel      French Restaurant   
17            7th     French Restaurant                 Garden   
18            8th                 Hotel      French Restaurant   
19            9th     French Restaurant                 Bakery   

            3rd Most Common Venue   4th Most Common Venue  \
0             Japanese Restaurant             Coffee Shop   
1                     Pizza Place                     Bar   
2                             Bar             Coffee Shop   
3                           Hotel         Thai Restaurant   
4             Japanese Restaurant      Italian Restaurant   
5                          Bakery       Korean Restaurant   
6              Italian Restaurant                  Bakery   
7              Italian Restaurant                Beer Bar   
8                             Bar                   Plaza   
9                             Bar              Restaurant   
10              French Restaurant              Art Museum   
11                     Restaurant      Italian Restaurant   
12  Vegetarian / Vegan Restaurant            Cocktail Bar   
13             Italian Restaurant                Wine Bar   
14                   Cocktail Bar                   Plaza   
15                       Wine Bar                  Bistro   
16                         Garden  Furniture / Home Store   
17                  Historic Site      Italian Restaurant   
18                            Bar     Japanese Restaurant   
19             Italian Restaurant            Cocktail Bar   

   5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0              Gastropub            Boxing Gym     Dim Sum Restaurant   
1                 Bistro          Cocktail Bar    Moroccan Restaurant   
2                  Hotel                  Park                 Garden   
3     Italian Restaurant                  Café       Asian Restaurant   
4              Wine Shop                Bistro  Vietnamese Restaurant   
5                  Plaza    Italian Restaurant    Japanese Restaurant   
6             Art Museum                 Plaza            Pizza Place   
7               Wine Bar                 Plaza                    Bar   
8            Coffee Shop                Bakery            Pizza Place   
9                   Café          Cocktail Bar                   Park   
10         Historic Site          Cocktail Bar               Boutique   
11                Bakery          Cocktail Bar                   Café   
12                   Bar           Coffee Shop              Gastropub   
13        Breakfast Spot                Bakery           Cocktail Bar   
14      Tapas Restaurant             Bookstore           Burger Joint   
15          Dessert Shop        Ice Cream Shop                    Bar   
16           Coffee Shop          Cupcake Shop       Department Store   
17              Tea 

#### 3. Clustering

In [44]:
# K Means method to cluster the Paris city into 5: set and run
kclusters = 5
arrond_grouped_clustering = arrond_LL.drop('Arrondissement', 1)
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(arrond_grouped_clustering)

kmeans.labels_[0:10]

array([0, 0, 2, 2, 3, 3, 3, 0, 0, 2], dtype=int32)

In [45]:
# add clustering labels
arrond_venues_sorted.insert(0, 'Cluster Label', kmeans.labels_)

arrond_merge = arrond_LL

# merge grouped with data to add latitude/longitude for each arrondissement
arrond_merge = arrond_merge.join(arrond_venues_sorted.set_index('Arrondissement'), on='Arrondissement')

# arrond_merge = arrond_merge.drop('Cluster',1) # accidentally added added another cluster column so this was to get rid of that extra column

arrond_merge.head(20)

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
0             1st  48.864614   2.334396              4                 Hotel   
1             2nd  48.868743   2.341688              3                 Hotel   
2             3rd  48.864212   2.360936              3     French Restaurant   
3             4th  48.856202   2.355619              1     French Restaurant   
4             5th  48.846059   2.344523              1     French Restaurant   
5             6th  48.850433   2.332951              0                 Hotel   
6             7th  48.857028   2.320195              0     French Restaurant   
7             8th  48.877316   2.317261              2                 Hotel   
8             9th  48.876019   2.339962              4     French Restaurant   
9            10th  48.876106   2.359910              0     French Restaurant   
10           11th  48.858416   2.379703              0     French Restaurant   
11           12th  48.839615   2.395752              2     French Restaurant   
12           13th  48.832397   2.355583              2     French Restaurant   
13           14th  48.833059   2.326959              3     French Restaurant   
14           15th  48.841370   2.300383              3     French Restaurant   
15           16th  48.863171   2.275765              3     French Restaurant   
16           17th  48.884224   2.322364              0     French Restaurant   
17           18th  48.890012   2.346467              0     French Restaurant   
18           19th  48.889343   2.384360              2     French Restaurant   
19           20th  48.865042   2.398929              4                   Bar   

    2nd Most Common Venue          3rd Most Common Venue  \
0                   Plaza              French Restaurant   
1       French Restaurant  Vegetarian / Vegan Restaurant   
2               Bookstore             Italian Restaurant   
3             Coffee Shop                   Cocktail Bar   
4                   Plaza                       Wine Bar   
5       French Restaurant                         Garden   
6                  Garden                  Historic Site   
7       French Restaurant                            Bar   
8                  Bakery             Italian Restaurant   
9                  Bakery            Japanese Restaurant   
10               Wine Bar                    Pizza Place   
11              Bookstore                            Bar   
12  Vietnamese Restaurant                          Hotel   
13                  Hotel            Japanese Restaurant   
14                  Hotel                         Bakery   
15                  Hotel             Italian Restaurant   
16                  Hotel             Italian Restaurant   
17     Italian Restaurant                            Bar   
18              Multiplex                            Bar   
19      French Restaurant                     Restaurant   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0               Art Museum         Historic Site          Cocktail Bar   
1             Cocktail Bar                   Bar           Coffee Shop   
2                 Wine Bar        Breakfast Spot                Bakery   
3                    Plaza      Tapas Restaurant             Bookstore   
4                   Bistro          Dessert Shop        Ice Cream Shop   
5   Furniture / Home Store           Coffee Shop          Cupcake Shop   
6       Italian Restaurant              Tea Room                 Plaza   
7      Japanese Restaurant    Italian Restaurant       Thai Restaurant   
8             Cocktail Bar   Indie Movie Theater                Bistro   
9              Coffee Shop             Gastropub            Boxing Gym   
10                     Bar                Bistro          Cocktail Bar   
11             Coffee Shop                 Hotel                  Park   
12         Thai Restaurant    Italian Restaurant                  Café   
13      Italian Restauran

In [46]:
cluster1 = arrond_merge.loc[arrond_merge['Cluster Label'] == 0]
cluster1

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
5             6th  48.850433   2.332951              0                 Hotel   
6             7th  48.857028   2.320195              0     French Restaurant   
9            10th  48.876106   2.359910              0     French Restaurant   
10           11th  48.858416   2.379703              0     French Restaurant   
16           17th  48.884224   2.322364              0     French Restaurant   
17           18th  48.890012   2.346467              0     French Restaurant   

   2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
5      French Restaurant                Garden  Furniture / Home Store   
6                 Garden         Historic Site      Italian Restaurant   
9                 Bakery   Japanese Restaurant             Coffee Shop   
10              Wine Bar           Pizza Place                     Bar   
16                 Hotel    Italian Restaurant                Beer Bar   
17    Italian Restaurant                   Bar                   Plaza   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
5            Coffee Shop          Cupcake Shop      Department Store   
6               Tea Room                 Plaza          Cocktail Bar   
9              Gastropub            Boxing Gym    Dim Sum Restaurant   
10                Bistro          Cocktail Bar   Moroccan Restaurant   
16              Wine Bar                 Plaza                   Bar   
17           Coffee Shop                Bakery           Pizza Place   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
5               Creperie           Tailor Shop           Gourmet Shop  
6                 Lounge           Pastry Shop              Hotel Bar  
9              Speakeasy  Cambodian Restaurant             Restaurant  
10              Beer Bar    Italian Restaurant                 Bakery  
16                Bakery            Street Art             Steakhouse  
17                Bistro            Restaurant           Dessert Shop

In [47]:
cluster2 = arrond_merge.loc[arrond_merge['Cluster Label'] == 1]

cluster2

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
3            4th  48.856202   2.355619              1     French Restaurant   
4            5th  48.846059   2.344523              1     French Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3           Coffee Shop          Cocktail Bar                 Plaza   
4                 Plaza              Wine Bar                Bistro   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3      Tapas Restaurant             Bookstore          Burger Joint   
4          Dessert Shop        Ice Cream Shop                   Bar   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3                  Café            Restaurant            Cheese Shop  
4              Tea Room    Seafood Restaurant               Fountain

In [48]:
cluster3 = arrond_merge.loc[arrond_merge['Cluster Label'] == 2]

cluster3

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
7             8th  48.877316   2.317261              2                 Hotel   
11           12th  48.839615   2.395752              2     French Restaurant   
12           13th  48.832397   2.355583              2     French Restaurant   
18           19th  48.889343   2.384360              2     French Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
7       French Restaurant                   Bar   Japanese Restaurant   
11              Bookstore                   Bar           Coffee Shop   
12  Vietnamese Restaurant                 Hotel       Thai Restaurant   
18              Multiplex                   Bar            Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
7     Italian Restaurant       Thai Restaurant                  Park   
11                 Hotel                  Park                Garden   
12    Italian Restaurant                  Café      Asian Restaurant   
18                  Café          Cocktail Bar                  Park   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
7                  Plaza          Gourmet Shop            Coffee Shop  
11  Gym / Fitness Center                Lounge               Creperie  
12    Chinese Restaurant                Bakery                    Bar  
18          Concert Hall           Music Venue            Pizza Place

In [49]:
cluster4 = arrond_merge.loc[arrond_merge['Cluster Label'] == 3]

cluster4

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
1             2nd  48.868743   2.341688              3                 Hotel   
2             3rd  48.864212   2.360936              3     French Restaurant   
13           14th  48.833059   2.326959              3     French Restaurant   
14           15th  48.841370   2.300383              3     French Restaurant   
15           16th  48.863171   2.275765              3     French Restaurant   

   2nd Most Common Venue          3rd Most Common Venue 4th Most Common Venue  \
1      French Restaurant  Vegetarian / Vegan Restaurant          Cocktail Bar   
2              Bookstore             Italian Restaurant              Wine Bar   
13                 Hotel            Japanese Restaurant    Italian Restaurant   
14                 Hotel                         Bakery     Korean Restaurant   
15                 Hotel             Italian Restaurant                Bakery   

   5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
1                    Bar           Coffee Shop              Gastropub   
2         Breakfast Spot                Bakery           Cocktail Bar   
13             Wine Shop                Bistro  Vietnamese Restaurant   
14                 Plaza    Italian Restaurant    Japanese Restaurant   
15            Art Museum                 Plaza            Pizza Place   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1       Seafood Restaurant        Sandwich Place        Bubble Tea Shop  
2   Furniture / Home Store    Seafood Restaurant         Sandwich Place  
13                     Bar           Pizza Place               Creperie  
14                    Park  Gym / Fitness Center                 Bistro  
15     Japanese Restaurant             Hotel Bar                   Café

In [50]:
cluster5 = arrond_merge.loc[arrond_merge['Cluster Label'] == 4]

cluster5

Arrondissement   Latitude  Longitude  Cluster Label 1st Most Common Venue  \
0             1st  48.864614   2.334396              4                 Hotel   
8             9th  48.876019   2.339962              4     French Restaurant   
19           20th  48.865042   2.398929              4                   Bar   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Plaza     French Restaurant            Art Museum   
8                 Bakery    Italian Restaurant          Cocktail Bar   
19     French Restaurant            Restaurant    Italian Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0          Historic Site          Cocktail Bar              Boutique   
8    Indie Movie Theater                Bistro           Cheese Shop   
19                Bakery          Cocktail Bar                  Café   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0          Women's Store          Dessert Shop                Theater  
8             Taco Place          Dessert Shop                  Hotel  
19    Mexican Restaurant             Bookstore  Vietnamese Restaurant

In [51]:
museum = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Museum','Art Museum', 'Science Museum', 'Exhibit', 'Art Gallery', 'History Museum'])]

outdoor_sights = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Bridge', 'Street Art','Plaza', 'Pedestrian Plaza', 'Scenic Lookout', 'Outdoor Sculpture', 'Theme Park Ride / Attraction', 'Canal', 'Park', 'Garden', 'Botanical Garden' ])]
                                   
fashion_store = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Department Store','Boutique',"Men's Store","Women's Store",'Cosmetics Shop', 'Clothing Store', 'Jewelry Store', 'Tailor Shop', 'Gift Shop', 'Shopping Mall'])]

night_life = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Nightclub', 'Hookah Bar', 'Jazz Club', 'Rock Club'])]

bike = arrond_venues.loc[arrond_venues['Venue Category'] == 'Bike Rental / Bike Share']                                   

relax = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Spa', 'Massage Studio'])]

asian_food = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Udon Restaurant', 'Japanese Restaurant', 'Asian Restaurant', 
                                                                     'Szechuan Restaurant', 'Korean Restaurant', 'Vietnamese Restaurant',
                                                                    'Thai Restaurant', 'Cambodian Restaurant', 'Sushi Restaurant',
                                                                    'Jiangxi Restaurant', 'Chinese Restaurant', 'Indian Restaurant'])]

world_food = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Modern European Restaurant', 'Italian Restaurant', 'Argentinian Restaurant', 'American Restaurant', 'Scandinavian Restaurant', 'Trattoria/Osteria' , 
                                                                     'Israeli Restaurant', 'Vegetarian / Vegan Restaurant', 'Seafood Restaurant', 'Lebanese Restaurant', 'Ethiopian Restaurant', 'Mexican Restaurant',
                                                                    'Breton Restaurant','Corsican Restaurant', 'Mediterranean Restaurant', 'Russian Restaurant', 'Tapas Restaurant', 'Falafel Restaurant', 'Moroccan Restaurant',
                                                                    'Turkish Restaurant', 'Portuguese Restaurant', 'Greek Restaurant', 'Brazilian Restaurant', 'Peruvian Restaurant', 'Comfort Food Restaurant', 'Steakhouse',
                                                                    'Basque Restaurant', 'Middle Eastern Restaurant', 'Arepa Restaurant', 'Southern / Soul Food Restaurant', 'African Restaurant', 'Gluten-free Restaurant'])]
                               
french = arrond_venues.loc[arrond_venues['Venue Category'].isin(['French Restaurant', 'Creperie','Cheese Shop', 'Provençal Restaurant', 'Bistro', 'Brasserie', 'Auvergne Restaurant'])]

dessert = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Ice Cream Shop','Pastry Shop', 'Bakery', 'Dessert Shop', 'Donut Shop', 'Chocolate Shop', 'Cupcake Shop'])] 
                           
drink = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Cocktail Bar', 'Beer Bar','Beer Store', 'Roof Deck', 'Wine Bar', 'Tea Room', 'Liquor Store', 'Wine Shop', 
                                                                'Bar', 'Gastropub', 'Speakeasy', 'Lounge', 'Beer Garden', 'Irish Pub', 'Champagne Bar', 'Hotel Bar', 'Vineyard'])]
cafe = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Café', 'Breakfast Spot', 'Coffe Shop', 'Tea Room'])]
                          
fast_food = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Burger Joint', 'Hot Dog Joint', 'Sandwich Place', 'Pizza Place', 
                                                                    'Fish & Chips Shop', 'Deli / Bodega', 'Taco Place', 'Food & Drink Shop',
                                                                   'BBQ Joint', 'Bagel Shop', 'Fast Food Restaurant', 'Diner', 'Food Truck'])]                 

market = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Farmers Market','Cheese Shop', 'Organic Grocery', 'Market', 'Supermarket'])]


historic_site = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Historic Site', 'Monument / Landmark'])]


perform = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Theater', 'Indie Movie Theater', 'Opera House', 'Comedy Club', 'Concert Hall', 'Music Venue', 'Performing Arts Venue'])]                 


lodging = arrond_venues.loc[arrond_venues['Venue Category'].isin(['Hotel', 'Hostel'])]


In [52]:
def map_with_arrond_and_points(points_df, arrondll):

    map_name = folium.Map(location = [48.8566101, 2.3514992], zoom_start = 12)
    
    map_name.choropleth(
        geo_data=paris,
        data=pop_2005,
        columns=['Arrondissement', 'Population'],
        key_on='feature.properties.nom',
        fill_color='PuBu', 
        fill_opacity=0.1, 
        line_opacity=0.5,)

#add points of interest markers to the Paris map
    for lat, long, points, cat in zip(points_df['Venue Latitude'], points_df['Venue Longitude'], 
                                 points_df['Venue'], points_df['Venue Category']):
        label = '{}, {}'.format(points, cat)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 7, 
            popup = label,
            color = 'yellow',
            fill = True,
            fill_color = 'blue',
            fill_opacity = 0.7,
            parse_html = False).add_to(map_name)
        
#add arrond markers to the Paris map
    for lat, long, arrond in zip(arrondll['Latitude'], arrondll['Longitude'], 
                                 arrondll['Arrondissement']):
        label = '{}'.format(arrond)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 5, 
            popup = label,
            color = 'white',
            fill = True,
            fill_color = 'green',
            fill_opacity = 0.5,
            parse_html = False).add_to(map_name)
        
        
    return map_name

#### 4. Result and conslusion

In [53]:
map_with_arrond_and_points(points_df = french, arrondll = arrond_LL)

In [54]:
map_with_arrond_and_points(points_df = cafe, arrondll = arrond_LL)

In [55]:
def map_with_arrond_and_points_v1(points_df, arrondll):

# Add the boundaries of the arrondissement
    map_name = folium.Map(location = [48.8566101, 2.3514992], zoom_start = 12)
    
    map_name.choropleth(
        geo_data=paris,
        data=pop_2005,
        columns=['Arrondissement', 'Population'],
        key_on='feature.properties.nom',
        fill_color='PuBu', 
        fill_opacity=0.1, 
        line_opacity=0.5,)

    # instantiate a mark cluster object for the incidents in the dataframe
    venues = plugins.MarkerCluster().add_to(map_name)

    # loop through the dataframe and add each data point to the mark cluster
    for lat, lng, name, cat in zip(points_df['Venue Latitude'], points_df['Venue Longitude'], 
                                 points_df['Venue'], points_df['Venue Category']):
        label = '{}, {}'.format(name, cat)
        label = folium.Popup(label, parse_html=True)
        folium.Marker(
            location=[lat, lng],
            icon=None,
            popup=label).add_to(venues)
        
        
#add arrond markers to the Paris map
    for lat, long, arrond in zip(arrondll['Latitude'], arrondll['Longitude'], 
                                 arrondll['Arrondissement']):
        label = '{}'.format(arrond)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 5, 
            popup = label,
            color = 'white',
            fill = True,
            fill_color = 'green',
            fill_opacity = 0.5,
            parse_html = False).add_to(map_name)
        
    return map_name

In [56]:
def map_with_arrond_and_points_v2(points_df, arrondll, landmarks):

# Add the boundaries of the arrondissement
    map_name = folium.Map(location = [48.8566101, 2.3514992], zoom_start = 12)
    
    map_name.choropleth(
        geo_data=paris,
        data=pop_2005,
        columns=['Arrondissement', 'Population'],
        key_on='feature.properties.nom',
        fill_color='PuBu', 
        fill_opacity=0.1, 
        line_opacity=0.5,)

    # instantiate a mark cluster object for the incidents in the dataframe
    venues = plugins.MarkerCluster().add_to(map_name)

    # loop through the dataframe and add each data point to the mark cluster
    for lat, lng, name, cat in zip(points_df['Venue Latitude'], points_df['Venue Longitude'], 
                                 points_df['Venue'], points_df['Venue Category']):
        label = '{}, {}'.format(name, cat)
        label = folium.Popup(label, parse_html=True)
        folium.Marker(
            location=[lat, lng],
            icon=None,
            popup=label).add_to(venues)
        
        
#add arrond markers to the Paris map
    for lat, long, arrond in zip(arrondll['Latitude'], arrondll['Longitude'], 
                                 arrondll['Arrondissement']):
        label = '{}'.format(arrond)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 5, 
            popup = label,
            color = 'white',
            fill = True,
            fill_color = 'green',
            fill_opacity = 0.5,
            parse_html = False).add_to(map_name)
        
#add landmarks of interest markers to the Paris map
    for lat, long, landmark in zip(landmarks['Latitude'], landmarks['Longitude'], 
                                 landmarks['Landmark']):
        label = '{}'.format(landmark)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, long],
            radius = 7, 
            popup = label,
            color = 'red',
            fill = True,
            fill_color = 'blue',
            fill_opacity = 0.7,
            parse_html = False).add_to(map_name)
        
    return map_name

In [57]:
map_with_arrond_and_points_v2(points_df = french, arrondll = arrond_LL, landmarks = landmarks_df)

In [58]:
map_with_arrond_and_points_v2(points_df = museum, arrondll = arrond_LL, landmarks = landmarks_df)

In [60]:

map_with_arrond_and_points_v2(points_df = dessert, arrondll = arrond_LL, landmarks = landmarks_df)

In [62]:
map_with_arrond_and_points_v1(points_df = historic_site, arrondll = arrond_LL)

In [64]:
map_with_arrond_and_points_v2(points_df = drink, arrondll = arrond_LL, landmarks = landmarks_df)

In [65]:
map_with_arrond_and_points_v2(points_df = cafe, arrondll = arrond_LL, landmarks = landmarks_df)

In [66]:
map_with_arrond_and_points_v2(points_df = fast_food, arrondll = arrond_LL, landmarks = landmarks_df)

In [68]:
map_with_arrond_and_points(fashion_store, arrond_LL)

In [69]:
map_with_arrond_and_points_v2(points_df = world_food, arrondll = arrond_LL, landmarks = landmarks_df)